# AudioLDM 2

From https://mp.weixin.qq.com/s/S8xs75FA4PlN-Ed2cgeCoA

In [1]:
import os
os.environ['HTTP_PROXY'] = 'http://proxy.vmware.com:3128'
os.environ['HTTPS_PROXY'] = 'http://proxy.vmware.com:3128'

In [2]:
pip install diffusers==0.21.4

  Obtaining dependency information for diffusers==0.21.4 from https://files.pythonhosted.org/packages/2e/ed/58a13f88dfcdd1bcfeabf44d4c9861979551339348e579fd6559c64b12e0/diffusers-0.21.4-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.5/1.5 MB 2.4 MB/s eta 0:00:0000:0100:010m
Note: you may need to restart the kernel to use updated packages.


In [2]:
from diffusers import AudioLDM2Pipeline

# model_id = "cvssp/audioldm2" # 文生音频
# model_id = "cvssp/audioldm2-music" # 文生音乐
model_id = "cvssp/audioldm2-large" # 文生音频
pipe = AudioLDM2Pipeline.from_pretrained(model_id)

[2023-10-12 07:35:39,098] [INFO] [real_accelerator.py:133:get_accelerator] Setting ds_accelerator to cuda (auto detect)


Fetching 26 files:   0%|          | 0/26 [00:00<?, ?it/s]

Loading pipeline components...:   0%|          | 0/11 [00:00<?, ?it/s]

Some weights of T5EncoderModel were not initialized from the model checkpoint at /home/jovyan/.cache/huggingface/hub/models--cvssp--audioldm2-large/snapshots/b9df26d805086b4dc9b428990e29f71a513598eb/text_encoder_2 and are newly initialized: ['encoder.embed_tokens.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [3]:
pipe.to("cuda")

AudioLDM2Pipeline {
  "_class_name": "AudioLDM2Pipeline",
  "_diffusers_version": "0.21.4",
  "_name_or_path": "cvssp/audioldm2-large",
  "feature_extractor": [
    "transformers",
    "ClapFeatureExtractor"
  ],
  "language_model": [
    "transformers",
    "GPT2Model"
  ],
  "projection_model": [
    "audioldm2",
    "AudioLDM2ProjectionModel"
  ],
  "scheduler": [
    "diffusers",
    "DDIMScheduler"
  ],
  "text_encoder": [
    "transformers",
    "ClapModel"
  ],
  "text_encoder_2": [
    "transformers",
    "T5EncoderModel"
  ],
  "tokenizer": [
    "transformers",
    "RobertaTokenizerFast"
  ],
  "tokenizer_2": [
    "transformers",
    "T5TokenizerFast"
  ],
  "unet": [
    "audioldm2",
    "AudioLDM2UNet2DConditionModel"
  ],
  "vae": [
    "diffusers",
    "AutoencoderKL"
  ],
  "vocoder": [
    "transformers",
    "SpeechT5HifiGan"
  ]
}

In [4]:
import torch

generator = torch.Generator("cuda").manual_seed(0)

In [5]:
prompt = "The sound of Brazilian samba drums with waves gently crashing in the background"

audio = pipe(prompt, audio_length_in_s=10.24, generator=generator).audios[0]

  0%|          | 0/200 [00:00<?, ?it/s]

In [6]:
from IPython.display import Audio

Audio(audio, rate=16000)

In [7]:
negative_prompt = "Low quality, average quality."

audio_neg = pipe(prompt, negative_prompt=negative_prompt, generator=generator.manual_seed(0)).audios[0]

  0%|          | 0/200 [00:00<?, ?it/s]

In [8]:
Audio(audio_neg, rate=16000)

## 优化 1: Flash 注意力

In [12]:
pip install torch==2.0.1

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 619.9/619.9 MB 513.5 kB/s eta 0:00:0000:0100:02
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.7/5.7 MB 9.0 MB/s eta 0:00:00:00:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.0/21.0 MB 7.4 MB/s eta 0:00:00:00:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 849.3/849.3 kB 9.3 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.8/11.8 MB 8.7 MB/s eta 0:00:00:00:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 557.1/557.1 MB 582.6 kB/s eta 0:00:0000:0100:05
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 317.1/317.1 MB 741.8 kB/s eta 0:00:0000:0100:02
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [9]:
audio_flash = pipe(prompt, negative_prompt=negative_prompt, generator=generator.manual_seed(0)).audios[0]

  0%|          | 0/200 [00:00<?, ?it/s]

In [10]:
Audio(audio_flash, rate=16000)

## 优化 2: 半精度

In [11]:
pipe = AudioLDM2Pipeline.from_pretrained(model_id, torch_dtype=torch.float16)

pipe.to("cuda")

Loading pipeline components...:   0%|          | 0/11 [00:00<?, ?it/s]

Some weights of T5EncoderModel were not initialized from the model checkpoint at /home/jovyan/.cache/huggingface/hub/models--cvssp--audioldm2/snapshots/6b532af9151603f2f6012cdbbe962731ef249e68/text_encoder_2 and are newly initialized: ['encoder.embed_tokens.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


AudioLDM2Pipeline {
  "_class_name": "AudioLDM2Pipeline",
  "_diffusers_version": "0.21.4",
  "_name_or_path": "cvssp/audioldm2",
  "feature_extractor": [
    "transformers",
    "ClapFeatureExtractor"
  ],
  "language_model": [
    "transformers",
    "GPT2Model"
  ],
  "projection_model": [
    "audioldm2",
    "AudioLDM2ProjectionModel"
  ],
  "scheduler": [
    "diffusers",
    "DDIMScheduler"
  ],
  "text_encoder": [
    "transformers",
    "ClapModel"
  ],
  "text_encoder_2": [
    "transformers",
    "T5EncoderModel"
  ],
  "tokenizer": [
    "transformers",
    "RobertaTokenizerFast"
  ],
  "tokenizer_2": [
    "transformers",
    "T5TokenizerFast"
  ],
  "unet": [
    "audioldm2",
    "AudioLDM2UNet2DConditionModel"
  ],
  "vae": [
    "diffusers",
    "AutoencoderKL"
  ],
  "vocoder": [
    "transformers",
    "SpeechT5HifiGan"
  ]
}

In [12]:
audio_f16 = pipe(prompt, negative_prompt=negative_prompt, generator=generator.manual_seed(0)).audios[0]

Audio(audio_f16, rate=16000)

  0%|          | 0/200 [00:00<?, ?it/s]

## 优化 3: Torch Compile

In [13]:
pipe.unet = torch.compile(pipe.unet, mode="reduce-overhead", fullgraph=True)

In [14]:
import torch._dynamo
torch._dynamo.config.suppress_errors = True

audio_comp = pipe(prompt, negative_prompt=negative_prompt, generator=generator.manual_seed(0)).audios[0]


  0%|          | 0/200 [00:00<?, ?it/s]

[2023-10-12 02:18:08,817] torch._dynamo.convert_frame: [ERROR] WON'T CONVERT forward /opt/conda/lib/python3.9/site-packages/diffusers/pipelines/audioldm2/modeling_audioldm2.py line 664 
due to: 
Traceback (most recent call last):
  File "/opt/conda/lib/python3.9/site-packages/torch/_subclasses/fake_tensor.py", line 403, in dyn_shape
    raise DynamicOutputShapeException(func)
torch._subclasses.fake_tensor.DynamicOutputShapeException: aten.repeat_interleave.Tensor

The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "/opt/conda/lib/python3.9/site-packages/torch/_dynamo/utils.py", line 1206, in run_node
    raise RuntimeError(
RuntimeError: Failed running call_module self_down_blocks_1_attentions_2_transformer_blocks_0(*(FakeTensor(FakeTensor(..., device='meta', size=(2, 1024, 256), dtype=torch.float16), cuda:0),), **{'attention_mask': None, 'encoder_hidden_states': FakeTensor(FakeTensor(..., device='meta', size=(2, 18, 1024), d

Unsupported: dynamic shape operator: aten.repeat_interleave.Tensor

from user code:
   File "/opt/conda/lib/python3.9/site-packages/diffusers/pipelines/audioldm2/modeling_audioldm2.py", line 1149, in forward
    hidden_states = self.attentions[i * num_attention_per_layer + idx](
  File "/opt/conda/lib/python3.9/site-packages/diffusers/models/transformer_2d.py", line 315, in forward
    hidden_states = block(

Set torch._dynamo.config.verbose=True for more information


In [15]:
torch.__version__

'2.0.1+cu117'

## 优化 4: 调度器

In [16]:
pipe.scheduler.compatibles

[diffusers.schedulers.scheduling_deis_multistep.DEISMultistepScheduler,
 diffusers.schedulers.scheduling_pndm.PNDMScheduler,
 diffusers.schedulers.scheduling_heun_discrete.HeunDiscreteScheduler,
 diffusers.schedulers.scheduling_ddpm.DDPMScheduler,
 diffusers.schedulers.scheduling_euler_ancestral_discrete.EulerAncestralDiscreteScheduler,
 diffusers.schedulers.scheduling_dpmsolver_singlestep.DPMSolverSinglestepScheduler,
 diffusers.schedulers.scheduling_euler_discrete.EulerDiscreteScheduler,
 diffusers.schedulers.scheduling_k_dpm_2_discrete.KDPM2DiscreteScheduler,
 diffusers.utils.dummy_torch_and_torchsde_objects.DPMSolverSDEScheduler,
 diffusers.schedulers.scheduling_ddim.DDIMScheduler,
 diffusers.schedulers.scheduling_dpmsolver_multistep.DPMSolverMultistepScheduler,
 diffusers.schedulers.scheduling_lms_discrete.LMSDiscreteScheduler,
 diffusers.schedulers.scheduling_unipc_multistep.UniPCMultistepScheduler,
 diffusers.schedulers.scheduling_k_dpm_2_ancestral_discrete.KDPM2AncestralDiscret

In [8]:
from diffusers import DPMSolverMultistepScheduler

pipe.scheduler = DPMSolverMultistepScheduler.from_config(pipe.scheduler.config)

In [9]:
audio_20 = pipe(prompt, negative_prompt=negative_prompt, num_inference_steps=20, generator=generator.manual_seed(0)).audios[0]

  0%|          | 0/20 [00:00<?, ?it/s]

In [10]:
Audio(audio_20, rate=16000)

## 生成一个 2.5 分钟 (150 秒) 的音频。我们通过设置 num_waveforms_per_prompt =4 来生成 4 个候选音频。然后根据它们的余弦相似度得分进行排名。生成的音频中第 0 个音频就是分数“最高”的音频。

In [11]:
pipe = AudioLDM2Pipeline.from_pretrained(model_id, torch_dtype=torch.float16)

pipe.to("cuda")

audio = pipe(prompt, negative_prompt=negative_prompt, num_waveforms_per_prompt=4, audio_length_in_s=150, num_inference_steps=20, generator=generator.manual_seed(0)).audios[0]

Loading pipeline components...:   0%|          | 0/11 [00:00<?, ?it/s]

Some weights of T5EncoderModel were not initialized from the model checkpoint at /home/jovyan/.cache/huggingface/hub/models--cvssp--audioldm2/snapshots/6b532af9151603f2f6012cdbbe962731ef249e68/text_encoder_2 and are newly initialized: ['encoder.embed_tokens.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


  0%|          | 0/20 [00:00<?, ?it/s]

In [12]:
Audio(audio, rate=16000)